In [1]:
%pylab
from star_cluster import StarCluster
from filterlists import * 
#from slugpy.cluster_slug import cluster_slug

#cs = cluster_slug(use_nebular=False,photsystem="Vega",libname="CLUSTERSLUG_MW")
#cs.add_filters(messa_m51_filters)

# for i in range(10):
#     sc = StarCluster(10**4,model="EFF",background=1e-2,rmax=30,scale_radius=1.0,shape=2.5)
#     plt.plot(np.linspace(6,9,101),[sc.measure_r50(count_photons=True,age=a,method='poisson') for a in np.logspace(6,9,101)]); plt.yscale('log')
#phot = sc.get_photometry(3e8,["ACS_F555W"])
#plt.scatter(np.log10(sc.masses),phot[:,0])
#plt.scatter(np.log10(sc.masses),phot[:,1])
#phot = sc.get_photometry(1e7)
#plt.plot(np.log10(np.sort(sc.masses)), phot[sc.masses.argsort()])
#sc.measure_bayesian(1e6,"Mass",cs=cs)

#rc, rb = sc.get_all_radii()
#sc.get_background_radii(),sc.get_cluster_radii()
#%timeit sc.fit_density_profile() #full_output=True)



Using matplotlib backend: TkAgg
%pylab is deprecated, use %matplotlib inline and import the required libraries.
Populating the interactive namespace from numpy and matplotlib


In [2]:
from slugpy.cluster_slug import cluster_slug
import numpy as np
cs = cluster_slug(use_nebular=False,photsystem="Vega")
cs.add_filters(messa_m51_filters)

In [3]:
#from random_cluster_population import *
from density_models import *
import numpy as np
from star_cluster import StarCluster
from filterlists import * 

#ML_age, ML = np.loadtxt("Bruzual_Charlot_2003_ML_vs_Age.csv").T

data = []
#data = list(np.load("mass_radius_measurements.npy"))
slopes = []
#for i in range(1):
while True:
    #masses, ages, gammas = random_cluster_population(100,Mmin=5e3)
    Mmin, Mmax = 2e3, 1e6
    tmin, tmax = 3e6,1e9
    rmax = 15
    nclusters = 100
    gammas = np.random.uniform(2.1,3,nclusters)
    x = np.random.rand(nclusters)
    true_masses = Mmax * Mmin / (Mmax * (1 - x) + Mmin * x)
    ages = 10**(np.log10(tmin)+np.log10(tmax/tmin)*np.random.rand(nclusters))
    r50s = []
    masses = []
    masses_ap = []
    true_radii = []
    tm = []
    ta = []
    measured_ages = []
    #true_masses =[]
    
    for mass, age, gamma in zip(true_masses,ages,gammas):
        #print(mass)
        numstars = int(mass/0.5+0.5)
        scale_radius = 3*(mass/1e4)**(1./3)/model_r50(gamma,1.,'EFF')
        sc = StarCluster(num_stars=numstars, scale_radius=scale_radius, shape=gamma, background=1e-2,model='EFF',rmax=rmax)
        sc.get_cluster_radii()
        measured_mass = 10**sc.measure_bayesian(age,"Mass",cs=cs)[1]
        #if measured_mass < 5e3: continue
        measured_age = 10**sc.measure_bayesian(age,"Age",cs=cs)[1]
        params = sc.fit_density_profile(count_photons=True, age=age)
        gamma_measured = params[3]
        scale_radius_measured = 10**params[2]
        r50 = sc.measure_r50(count_photons=True,age=age)
        #if measured_age > 3e8 or measured_age < 1e7: continue
        masses_ap.append(measured_mass)        
        fac = mass_aperture_fac(gamma_measured,scale_radius_measured,rmax,'EFF')
        print(mass,measured_mass,gamma,gamma_measured, fac)
        measured_mass *= fac #mass_aperture_fac(gamma_measured,scale_radius_measured,rmax,'EFF')

        masses.append(measured_mass)        
        r50s.append(r50)
        tm.append(mass)
        ta.append(age)
        true_radii.append(3*(mass/1e4)**(1./3))
        measured_ages.append(measured_age)
    cut = np.isfinite(r50s) * (np.array(r50s)<100) * (np.array(r50s) > 0.1)
    slopes.append(np.polyfit(np.log10(masses)[cut],np.log10(r50s)[cut],1)[0])
    data.append([true_masses,true_radii,ages,gammas,masses,masses_ap,r50s,measured_ages])
    np.save("mass_radius_measurements.npy",data)
    print(slopes[-1])
print(np.median(slopes),np.std(slopes))

/home/mgrudic/code/cluster_profile_sim_dev/get_isochrone.py:136: NumbaExperimentalFeatureWarning: First-class function type feature is experimental
  mgrid1 = isochrone_grid[age_idx1, :, 0]
/home/mgrudic/code/cluster_profile_sim_dev/lossfuncs.py:45: RuntimeWarning: invalid value encountered in divide
  mu


2646.5070289236933 2315.516319876151 2.1058999413531603 4.9137453435676415 1.0000002345508574
3936.0463935250427 7130.306488545797 2.456074134622448 3.7063806182265173 1.0064959382934742


/home/mgrudic/code/cluster_profile_sim_dev/density_models.py:62: RuntimeWarning: overflow encountered in scalar power
  return np.sqrt(2 ** (2 / (gamma - 2)) - 1) * scale_radius


5886.469609358655 11926.445479342117 2.914522057428341 2.0000001574541466 2145966.986524009
8585.638233419293 5115.379797809372 2.5090278417586256 2.668508175602639 1.150651826190312
6850.373838284012 2938.87250505141 2.170641553598129 2.4626783207425267 1.0960265480277027
6523.2105628859845 4202.1631609075885 2.30640430466964 2.041452182612765 6.7445979046982165
3751.019906269197 2062.384890522467 2.5513580954644275 3.1763797766519413 1.033252519328354
3371.7083164702863 3690.223666758161 2.2627039318749547 2.084483979052322 2.6850430298702963
2414.0936530458052 11511.710740295961 2.3075123613471873 20.000000000000004 1.0
4879.229273223676 4082.0192937023685 2.6508830689029357 2.6751459006431744 1.1618178630791223
2294.77953890919 2954.199085817093 2.4658819056238492 19.999999971086044 1.0000000000059912
2551.4782732368585 1760.1958251358863 2.4003102305029103 2.3179533811740383 1.3733224736780607
3978.9068857101984 2994.879565796132 2.846039032529536 3.3072300165826376 1.043242815392

/home/mgrudic/code/cluster_profile_sim_dev/star_cluster.py:307: OptimizeWarning: Initial guess is not within the specified bounds
  sol = minimize(


3414.411163930759 2543.311709017134 2.1236511553496733 20.000000000000004 1.0
40773.2045985362 46959.460789760524 2.7173559472694904 3.909294774228528 1.0537421565521816
3111.265929748102 8012.930352960103 2.241221386550441 2.0000000029721208 63028961.5327019
3077.692314153601 2187.7466861556045 2.4298643609982937 2.6871664654208685 1.0945767175717558
5391.417714878958 6297.228735444636 2.876139647474501 4.259575846873629 1.0165175862194902
4254.267568578788 2351.657980682461 2.7254417020793733 2.080584871507061 4.385541285467074
2507.3490112352856 1613.986640676338 2.187391047416684 2.234102628278652 1.3463771996746603
2385.0737053454186 4372.687943489994 2.8112472176654135 2.000000024514845 13984040.147334576
3514.355542206413 2554.8509562366858 2.9594795432928014 3.9411533017817675 1.0085739175804236
2413.1699581037083 1853.729942896019 2.940405993886633 2.790791944378738 1.138486965176374
2118.961114008564 4565.791318844737 2.8097780885103774 19.999999557540598 1.0000000000000537
3

KeyboardInterrupt: 

In [21]:
len(data[0])

7

In [4]:
np.load("mass_radius_measurements.npy").shape
#data.shape

(778, 8, 100)

In [5]:
#sc.measure_bayesian(age,"Mass",cs=cs)
plt.figure(figsize=(4,4))
plt.loglog(masses,r50s,'.',label="Measured")
plt.loglog(tm,3*(np.array(tm)/1e4)**(1./3),'.',label="True")
for i in range(len(tm)):
    plt.loglog([tm[i],masses[i]],[3*(tm[i]/1e4)**(1./3),r50s[i]],color='black',alpha=0.3)
plt.xlabel(r"$M\,\left(M_\odot\right)$")
plt.ylabel(r"$R_{\rm eff}\,\left(\rm pc\right)$")
plt.legend()
cut = np.isfinite(r50s) * (np.array(r50s)<100) * (np.array(r50s) > 0.1)
#print(cut.sum())
fit = np.polyfit(np.log10(masses)[cut],np.log10(r50s)[cut],1)
logr_model = np.polyval(fit, np.log10(masses)[cut])
np.std(logr_model - np.log10(r50s)[cut]), fit[0]


(0.384098073084777, 0.8918501546010247)

In [23]:
np.polyval(fit, np.log10(masses)[cut])

TypeError: iteration over a 0-d array

In [4]:
import pickle
f
filt, track, grids = pickle.load(
    open(f"lumgrids/mass_lum_grid_{filt}_{track}.dump", "rb")
)
mgrid, Lgrid = grids[age_yr]
logmgrid = np.log10(mgrid)
logLgrid = np.log10(Lgrid)
mmax = mgrid[np.isfinite(logLgrid)].max()

NameError: name 'filt' is not defined

In [5]:
sc.num_stars

100000

In [6]:
1 - (1 + np.inf * np.inf) ** (1 - 0.5 * 2.5)


1.0